In [18]:
import sys
import pathlib
import pandas as pd
prefix='new-lincRNAs'
appdir='~/dev/fastq/dlinct/'
paths_table=appdir + 'test_get_features/features/new-lincRNAs/paths.txt'
bed_path=appdir + 'new-lincRNAs.bed'
outpath=appdir + 'test_get_features/features/new-lincRNAs/'

In [10]:
readin=pd.read_csv(paths_table, delimiter='\t', header=None)
# for index, rows in readin.iterrows():
#     readin.iloc[index, [1]] = appdir + 'lncrna/' + rows[0] + '.tsv'

readin.head(15)

0                                                  1
0               CAGE_neg  ~/dev/fastq/dlinct/test_get_features/features/...
1   CAGE_neg_whole_trans  ~/dev/fastq/dlinct/test_get_features/features/...
2               CAGE_pos  ~/dev/fastq/dlinct/test_get_features/features/...
3   CAGE_pos_whole_trans  ~/dev/fastq/dlinct/test_get_features/features/...
4                 GCcont  ~/dev/fastq/dlinct/test_get_features/features/...
5             H3K4me3_S2  ~/dev/fastq/dlinct/test_get_features/features/...
6              JASPAR_TF  ~/dev/fastq/dlinct/test_get_features/features/...
7            phastCons27  ~/dev/fastq/dlinct/test_get_features/features/...
8              phyloP124  ~/dev/fastq/dlinct/test_get_features/features/...
9               phyloP27  ~/dev/fastq/dlinct/test_get_features/features/...
10               Pol2_S2  ~/dev/fastq/dlinct/test_get_features/features/...
11                 ReMap  ~/dev/fastq/dlinct/test_get_features/features/...

In [11]:
bed=pd.read_csv(bed_path, delimiter='\t', header=None)
bed.columns = ["chr", "start", "end", "name", "score", "strand"]

# Define column names
bw_cols=["name", "size", "covered_bases", "sum", "mean0", "mean", "min", "max"]
bb_cols=["name", "covered_percent", "mean", "min", "max"]

In [12]:
# Create dataframes from extracted features
for i in range(len(readin)):
    if readin.iloc[i,0] == 'GCcont':
        df_gc=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_gc.columns=bw_cols
    elif readin.iloc[i,0] == 'phastCons27':
        df_pc27=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_pc27.columns=bw_cols
    elif readin.iloc[i,0] == 'phyloP27':
        df_pp27=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_pp27.columns=bw_cols
    elif readin.iloc[i,0] == 'phyloP124':
        df_pp124=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_pp124.columns=bw_cols
    elif readin.iloc[i,0] == 'Pol2_S2':
        df_pol2=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_pol2.columns=bw_cols
    elif readin.iloc[i,0] == 'H3K4me3_S2':
        df_me3=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_me3.columns=bw_cols
    elif readin.iloc[i,0] == 'CAGE_pos_whole_trans':
        df_posTSS_wt=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_posTSS_wt.columns=bw_cols
    elif readin.iloc[i,0] == 'CAGE_neg_whole_trans':
        df_negTSS_wt=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_negTSS_wt.columns=bw_cols
    elif readin.iloc[i,0] == 'ReMap':
        df_re=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_re.columns=bb_cols
    elif readin.iloc[i,0] == 'JASPAR_TF':
        df_tf=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_tf.columns=bb_cols
    elif readin.iloc[i,0] == 'CAGE_pos':
        df_posTSS=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None)
        df_posTSS.columns=["name", "startPosTSS"]
    elif readin.iloc[i,0] == 'CAGE_neg':
        df_negTSS=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None, na_values=0)
        df_negTSS.columns=["name", "endNegTSS"]
    elif readin.iloc[i,0] == 'RNAfold':
        df_2s=pd.read_csv(readin.iloc[i,1], delimiter='\t', header=None, na_values=0)
        df_2s.columns=["name", "mfe"]

# Function to append values of df with different row numbers
def append_columns(ref_df, query_df, ref_col, append_col, **kwargs):
    ref_col = str(ref_col)
    append_col = str(append_col)
    new_col_name = kwargs.get('new_col_name', None)    
    try: new_col_name
    except NameError: new_col_name = None
    if new_col_name is None:
        new_col_name = append_col
    
    df=pd.DataFrame({})
    for name, group in query_df.groupby(ref_col):
        buffer_df = pd.DataFrame({ref_col: group[ref_col][:1]})
        i = 0
        for index, value in group[append_col].iteritems():
            i += 1
            string = new_col_name
            buffer_df[string] = value
        df = df.append(buffer_df)
    features = pd.merge(ref_df, df, how='left', on=ref_col)
    return features

def append_all_cols(ref_df, query_df, ref_col):
    ref_col = str(ref_col)
    for i in range(len(query_df.columns)):
        if query_df.columns[i] == ref_col:
            ref_col = query_df.columns[i]
            for i in range(len(query_df.columns)):
                if query_df.columns[i] != ref_col:
                    append_col = query_df.columns[i]
                    features = append_columns(ref_df, query_df, ref_col, append_col)
                    ref_df = features
    return features

In [13]:
df_gc.head()

name  size  covered_bases  sum  mean0  mean  min  max
0  TCONS_00000001.1.   295              0    0    0.0   0.0    0    0
1  TCONS_00000002.1.   499              0    0    0.0   0.0    0    0
2  TCONS_00000003.1.   579              0    0    0.0   0.0    0    0
3  TCONS_00000004.1.   496              0    0    0.0   0.0    0    0
4  TCONS_00000005.1.   386              0    0    0.0   0.0    0    0

In [14]:
## Create the features table

features = bed["name"]
features = append_columns(features, bed, 'name', 'start')
features = append_columns(features, bed, 'name', 'end')
features["length"] = features["end"] - features["start"]

# Incorporate secondary structure values
#features = append_all_cols(features, df_2s, 'name')

### Drop all rows that have no computed RNA fold
features.dropna(axis=0, how='any', inplace=True)

# Incorporate TSS peaks near ('ofsset' +/- 'start'/'end')
features = append_all_cols(features, df_posTSS, 'name')
features = append_all_cols(features, df_negTSS, 'name')

# Find best TSS from the positive and negative TSS values arround 5' and 3' of transcript
tss_peak = features[["startPosTSS", "endNegTSS"]]
tss_peak = abs(tss_peak)
tss_peak = tss_peak.max(axis=1)
features["bestTSS"] = tss_peak
features.drop(columns=["startPosTSS", "endNegTSS"], inplace=True)

# Incorporate TSS peaks inside the whole transcript
features = append_columns(features, df_posTSS_wt, 'name', 'max', new_col_name='PosTSS_inside')
features = append_columns(features, df_negTSS_wt, 'name', 'min', new_col_name='NegTSS_inside')

# Find best TSS inside the transcript itself
tss_peak_ins = features[["PosTSS_inside", "NegTSS_inside"]]
tss_peak_ins = abs(tss_peak_ins)
tss_peak_ins = tss_peak_ins.max(axis=1)
features["bestTSS_inside"] = tss_peak_ins
features.drop(columns=["PosTSS_inside", "NegTSS_inside"], inplace=True)

# Incorporate best metric for each queried bigWig or bigBed files
features = append_columns(features, df_gc, 'name', 'mean', new_col_name='mean_gc')
features = append_columns(features, df_re, 'name', 'mean', new_col_name='mean_remap')
features = append_columns(features, df_me3, 'name', 'covered_bases', new_col_name='cov_me3')
features["cov_me3"] = features["cov_me3"] / features["length"]
features = append_columns(features, df_tf, 'name', 'covered_percent', new_col_name='cov_tfbs')
features = append_columns(features, df_pol2, 'name', 'covered_bases', new_col_name='cov_pol2')
features["cov_pol2"] = features["cov_pol2"] / features["length"]
features = append_columns(features, df_pc27, 'name', 'mean0', new_col_name='mean_pcons27')
features = append_columns(features, df_pp27, 'name', 'mean0', new_col_name='mean_pPcons27')
features = append_columns(features, df_pp124, 'name', 'mean0', new_col_name='mean_pPcons124')

features.head(25)

/tmp/ipykernel_25854/3262655945.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(buffer_df)
/tmp/ipykernel_25854/3262655945.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(buffer_df)
/tmp/ipykernel_25854/3262655945.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(buffer_df)
/tmp/ipykernel_25854/3262655945.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(buffer_df)
/tmp/ipykernel_25854/3262655945.py:61: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(buffer_df)


name  start   end  length  bestTSS  bestTSS_inside  mean_gc  \
0   TCONS_00000001.1.    638   933     295      NaN               0      0.0   
1   TCONS_00000002.1.      0   499     499      NaN               0      0.0   
2   TCONS_00000003.1.   1389  1968     579      NaN               0      0.0   
3   TCONS_00000004.1.      0   496     496      NaN               0      0.0   
4   TCONS_00000005.1.     92   478     386      NaN               0      0.0   
5   TCONS_00000006.1.      0   243     243      NaN               0      0.0   
6   TCONS_00000008.1.      4    85      81      NaN               0      0.0   
7   TCONS_00000008.2.    145  1125     980      NaN               0      0.0   
8   TCONS_00000009.1.   1306  1605     299      NaN               0      0.0   
9   TCONS_00000009.2.   1665  2163     498      NaN               0      0.0   
10  TCONS_00000010.1.      1   271     270      NaN               0      0.0   
11  TCONS_00000011.1.    217   271      54      NaN               0      0.0   
12  TCONS_00000012.1.    625   725     100      NaN               0      0.0   
13  TCONS_00000011.2.    630  1609     979      NaN               0      0.0   
14  TCONS_00000012.2.   1083  1609     526      NaN               0      0.0   
15  TCONS_00000010.2.   1344  1609     265      NaN               0      0.0   
16  TCONS_00000013.1.      1   181     180      NaN               0      0.0   
17  TCONS_00000014.1.     44  1503    1459      NaN               0      0.0   
18  TCONS_00000015.1.      0   217     217      NaN               0      0.0   
19  TCONS_00000016.1.    527   873     346      NaN               0      0.0   
20  TCONS_00000018.1.      0   722     722      NaN               0      0.0   
21  TCONS_00000017.1.      0  1172    1172      NaN               0      0.0   
22  TCONS_00000018.2.    840  1172     332      NaN               0      0.0   
23  TCONS_00000019.1.    735  1331     596      NaN               0      0.0   
24  TCONS_00000020.1.    662   864     202      NaN               0      0.0   

    mean_remap  cov_me3  cov_tfbs  cov_pol2  mean_pcons27  mean_pPcons27  \
0          NaN      0.0       NaN       0.0           0.0            0.0   
1          NaN      0.0       NaN       0.0           0.0            0.0   
2          NaN      0.0       NaN       0.0           0.0            0.0   
3          NaN      0.0       NaN       0.0           0.0            0.0   
4          NaN      0.0       NaN       0.0           0.0            0.0   
5          NaN      0.0       NaN       0.0           0.0            0.0   
6          NaN      0.0       NaN       0.0           0.0            0.0   
7          NaN      0.0       NaN       0.0           0.0            0.0   
8          NaN      0.0       NaN       0.0           0.0            0.0   
9          NaN      0.0       NaN       0.0           0.0            0.0   
10         NaN      0.0       NaN       0.0           0.0            0.0   
11         NaN      0.0       NaN       0.0           0.0            0.0   
12         NaN      0.0       NaN       0.0           0.0            0.0   
13         NaN      0.0       NaN       0.0           0.0            0.0   
14         NaN      0.0       NaN       0.0           0.0            0.0   
15         NaN      0.0       NaN       0.0           0.0            0.0   
16         NaN      0.0       NaN       0.0           0.0            0.0   
17         NaN      0.0       NaN       0.0           0.0            0.0   
18         NaN      0.0       NaN       0.0           0.0            0.0   
19         NaN      0.0       NaN       0.0           0.0            0.0   
20         NaN      0.0       NaN       0.0           0.0            0.0   
21         NaN      0.0       NaN       0.0           0.0            0.0   
22         NaN      0.0       NaN       0.0           0.0            0.0   
23         NaN      0.0       NaN       0.0           0.0            0.0   
24         NaN      0.0       NaN   

In [16]:
total=len(features)
total

1801

In [22]:
final_features=features.fillna(0)
final_features.head()

name     start       end  length  bestTSS  bestTSS_inside  \
0     TCONS_00000001.1.       638       933     295      0.0               0   
1     TCONS_00000002.1.         0       499     499      0.0               0   
2     TCONS_00000003.1.      1389      1968     579      0.0               0   
3     TCONS_00000004.1.         0       496     496      0.0               0   
4     TCONS_00000005.1.        92       478     386      0.0               0   
...                 ...       ...       ...     ...      ...             ...   
1345  TCONS_00035836.2.  23987517  23987691     174     35.0             470   
1346  TCONS_00035837.2.  23987517  23987691     174     35.0             470   
1347  TCONS_00035835.2.  23987741  23988199     458     74.0              74   
1348  TCONS_00035836.3.  23987741  23988199     458     74.0              74   
1349  TCONS_00035837.3.  23987741  23988199     458     74.0              74   

      mean_gc  mean_remap   cov_me3  cov_tfbs  cov_pol2  mean_pcons27  \
0      0.0000       0.000  0.000000  0.000000  0.000000           0.0   
1      0.0000       0.000  0.000000  0.000000  0.000000           0.0   
2      0.0000       0.000  0.000000  0.000000  0.000000           0.0   
3      0.0000       0.000  0.000000  0.000000  0.000000           0.0   
4      0.0000       0.000  0.000000  0.000000  0.000000           0.0   
...       ...         ...       ...       ...       ...           ...   
1345  32.1839     426.943  0.603448  0.988506  0.885057           0.0   
1346  32.1839     426.943  0.603448  0.988506  0.885057           0.0   
1347  35.8515      77.285  1.000000  0.978166  0.034934           0.0   
1348  35.8515      77.285  1.000000  0.978166  0.034934           0.0   
1349  35.8515      77.285  1.000000  0.978166  0.034934           0.0   

      mean_pPcons27  mean_pPcons124  
0               0.0        0.000000  
1               0.0        0.000000  
2               0.0        0.000000  
3               0.0        0.000000  
4               0.0        0.000000  
...             ...             ...  
1345            0.0        0.243408  
1346            0.0        0.243408  
1347            0.0        0.381616  
1348            0.0        0.381616  
1349            0.0        0.381616  

[1350 rows x 14 columns]

In [20]:
final_features.to_csv(outpath + '/' + prefix + '.csv', index=False)